# Questions

- Which classroom is the most utilized?
- Which classes go over capacity the most? (cap>0 use remainder to indicate overage)
- Which professors has the most diverse courseload?
- Which days are the most/least popular for classes?
- Which teacher has taught the most students? (via actual, not cap)
- Which classes are attracting less than 10 students? (> 0)

In [1]:
%load_ext sql
%sql sqlite:///CourseDataWarehouse.db

'Connected: @CourseDataWarehouse.db'

In [2]:
%%sql
attach Database 'CourseData.db' AS DB

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [3]:
%%sql
SELECT *
FROM DB.LOCATIONS
LIMIT 5;

 * sqlite:///CourseDataWarehouse.db
Done.


[(1, 'BCC 200'), (2, 'BD '), (3, 'BH '), (4, 'BH BY ARR'), (5, 'BLM 112')]

# Create Tables

In [4]:
%%sql

DROP TABLE IF EXISTS PROGRAMS_DW;
DROP TABLE IF EXISTS PROFESSORS_DW;
DROP TABLE IF EXISTS LOCATIONS_DW;
DROP TABLE IF EXISTS TIMECODES_DW;
DROP TABLE IF EXISTS COURSES_DW;
DROP TABLE IF EXISTS CLASS_FACTS;

 * sqlite:///CourseDataWarehouse.db
Done.
Done.
Done.
Done.
Done.
Done.


[]

In [5]:
%%sql

CREATE TABLE PROGRAMS_DW (
    Program_id INTEGER PRIMARY KEY,
    program_code TEXT NOT NULL,
    program_name TEXT NOT NULL
);

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [6]:
%%sql

CREATE TABLE PROFESSORS_DW (
    Professor_id INTEGER PRIMARY KEY,
    Name TEXT NOT NULL
);

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [7]:
%%sql

CREATE TABLE LOCATIONS_DW (
    Location_id INTEGER PRIMARY KEY,
    location TEXT NOT NULL
);

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [8]:
%%sql

CREATE TABLE TIMECODES_DW (
    Timecode_id INTEGER PRIMARY KEY,
    Day TEXT,
    Start TEXT NOT NULL,
    End TEXT NOT NULL
);

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [9]:
%%sql

CREATE TABLE COURSES_DW (
    Course_id INTEGER PRIMARY KEY, 
    CatalogYear TEXT NOT NULL,
    Catalog_id TEXT NOT NULL,
    Course_title TEXT NOT NULL,
    Credits TEXT NOT NULL
);

 * sqlite:///CourseDataWarehouse.db
Done.


[]

In [10]:
%%sql

CREATE TABLE CLASS_FACTS_DW (
    Course_id INTEGER,
    Program_id INTEGER,
    Location_id INTEGER,
    Professor_id INTEGER,
    Timecode_id INTEGER,
    CatalogYear TEXT NOT NULL,
    Term TEXT NOT NULL,
    Credits REAL,
    Section TEXT NOT NULL,
    Cap INTEGER NOT NULL,
    Actual INTEGER NOT NULL,
    Remaining INTEGER NOT NULL,
    Timecodes TEXT,
    Count_courses INTEGER,
    Num_students INTEGER,
    Count_location INTEGER,
    FOREIGN KEY (Course_id) REFERENCES COURSES_DW(Course_id),
    FOREIGN KEY (Program_id) REFERENCES PROGRAMS_DW(Program_id),
    FOREIGN KEY (Location_id) REFERENCES LOCATIONS_DW(Location_id),
    FOREIGN KEY (Professor_id) REFERENCES PROFESSORS_DW(Professor_id),
    FOREIGN KEY (Timecode_id) REFERENCES TIMECODES_DW(Timecode_id)   
);

 * sqlite:///CourseDataWarehouse.db
Done.


[]

# POPULATE TABLES

In [11]:
%%sql

INSERT INTO PROGRAMS_DW(program_name,program_code)
    SELECT DISTINCT program_name,program_code
    FROM DB.PROGRAMS;
SELECT * FROM PROGRAMS_DW LIMIT 5;

 * sqlite:///CourseDataWarehouse.db
83 rows affected.
Done.


[(1, 'AC', 'Accounting'),
 (2, 'AE', 'Applied Ethics'),
 (3, 'AH', 'Art History'),
 (4, 'AN', 'Asian Studies'),
 (5, 'AR', 'Arabic')]

In [12]:
%%sql

INSERT INTO PROFESSORS_DW(Name)
    SELECT DISTINCT Name
    FROM DB.PROFESSORS;
SELECT * FROM PROFESSORS_DW LIMIT 5;

 * sqlite:///CourseDataWarehouse.db
1104 rows affected.
Done.


[(1, 'Michael P.  Coyne'),
 (2, 'Rebecca I.  Bloch'),
 (3, 'Paul   Caster'),
 (4, 'Jo Ann   Drusbosky'),
 (5, 'Arleen N.  Kardos')]

In [13]:
%%sql

INSERT INTO LOCATIONS_DW(location)
    SELECT DISTINCT location
    FROM DB.LOCATIONS;
SELECT * FROM LOCATIONS_DW LIMIT 5;

 * sqlite:///CourseDataWarehouse.db
207 rows affected.
Done.


[(1, 'BCC 200'), (2, 'BD '), (3, 'BH '), (4, 'BH BY ARR'), (5, 'BLM 112')]

In [14]:
%%sql

INSERT INTO COURSES_DW(CatalogYear,Catalog_id,Course_title,Credits)
    SELECT DISTINCT CatalogYear,Catalog_id,Course_title,Credits
    FROM DB.COURSES;
SELECT * FROM COURSES_DW LIMIT 15;

 * sqlite:///CourseDataWarehouse.db
4440 rows affected.
Done.


[(1, '2017_2018', 'AN 0301', 'Independent Study', '1-3 Credits'),
 (2, '2017_2018', 'AN 0310', 'Asian Studies Seminar', '3 Credits'),
 (3, '2017_2018', 'BU 0211', 'Legal Environment of Business', '3 Credits'),
 (4, '2017_2018', 'BU 0220', 'Environmental Law and Policy', '3 Credits'),
 (5, '2017_2018', 'BU 0311', 'The Law of Contracts, Sales, and Property', '3 Credits'),
 (6, '2017_2018', 'BU 0312', 'The Law of Business Organizations and Financial Transactions', '3 Credits'),
 (7, '2017_2018', 'BU 0320', 'Employment Law and Discrimination in the Workplace', '3 Credits'),
 (8, '2017_2018', 'BU 0391', 'Seminar in Business Law and Ethics', '3 Credits'),
 (9, '2017_2018', 'BL 0101', 'Black Lives Matter', '3 Credits'),
 (10, '2017_2018', 'BL 0398', 'Independent Study', '1-3 Credits'),
 (11, '2017_2018', 'BEN 0201', 'Biomechanics', '3 Credits'),
 (12, '2017_2018', 'BEN 0300', 'Biomedical Instrumentation', '4 Credits'),
 (13, '2017_2018', 'BEN 0331', 'Biomedical Signal Processing', '3 Credits'),
 (14, '2017_2018', 'BEN 0332', 'Biomedical Imaging', '3 Credits'),
 (15, '2017_2018', 'BEN 0333', 'Biomedical Visualization', '3 Credits')]

In [16]:
%%sql
DELETE FROM TIMECODES_DW;
INSERT INTO TIMECODES_DW(Day,Start,End)
    SELECT DISTINCT Day,time(Start) AS StartTime,time(End) AS EndTime
    FROM DB.MEETINGS
    ORDER BY Day, StartTime, EndTime;
SELECT * FROM TIMECODES_DW LIMIT 15;

 * sqlite:///CourseDataWarehouse.db
0 rows affected.
1090 rows affected.
Done.


[(1, 'F', '07:00:00', '10:00:00'),
 (2, 'F', '07:00:00', '11:00:00'),
 (3, 'F', '07:00:00', '12:15:00'),
 (4, 'F', '07:00:00', '13:00:00'),
 (5, 'F', '07:00:00', '14:00:00'),
 (6, 'F', '07:00:00', '15:00:00'),
 (7, 'F', '07:00:00', '17:30:00'),
 (8, 'F', '07:45:00', '10:15:00'),
 (9, 'F', '07:55:00', '10:55:00'),
 (10, 'F', '08:00:00', '08:30:00'),
 (11, 'F', '08:00:00', '08:50:00'),
 (12, 'F', '08:00:00', '09:15:00'),
 (13, 'F', '08:00:00', '10:00:00'),
 (14, 'F', '08:00:00', '10:30:00'),
 (15, 'F', '08:00:00', '11:00:00')]

In [ ]:
%%sql

-- INSERT INTO CLASS_FACTS(Course_id,Program_id,Location_id,Professor_id,Timecode_id,CatalogYear,Term,Credits,Section,Cap,Actual,Remaining,Timecodes,Count_courses,Num_students,Count_location)
    
    SELECT DISTINCT CatalogYear, DB.Term, DB.Credits, DB.Section, DB.Cap, DB.Actual, DB.Remaining, DB.Timecodes, 
    FROM 
        JOIN COURSES_DW USING(Course_id)
        JOIN PROGRAM_DW USING(Program_id)
        JOIN LOCATIONS_DW USING(Location_id)
        JOIN PROFESSORS_DW USING(Professor_id)
        JOIN TIMECODES_DW USING(Timecode_id)
        JOIN DB.MEETINGS USING()

In [26]:
%%sql
SELECT DISTINCT Day,time(DB.MEETINGS.Start) AS StartTime,time(DB.MEETINGS.End) AS EndTime, Offering_id,Timecode_id
    FROM DB.MEETINGS
    JOIN DB.COURSE_OFFERINGS USING(Offering_id)
    JOIN TIMECODES_DW USING(Day)
WHERE TIMECODES_DW.Day = Day AND TIMECODES_DW.Start = StartTime AND TIMECODES_DW.End = EndTime
    ORDER BY Day, StartTime, EndTime;

 * sqlite:///CourseDataWarehouse.db
Done.


[('F', '07:00:00', '10:00:00', 15426, 1),
 ('F', '07:00:00', '11:00:00', 15426, 2),
 ('F', '07:00:00', '12:15:00', 8479, 3),
 ('F', '07:00:00', '12:15:00', 9905, 3),
 ('F', '07:00:00', '12:15:00', 11338, 3),
 ('F', '07:00:00', '12:15:00', 11339, 3),
 ('F', '07:00:00', '13:00:00', 1074, 4),
 ('F', '07:00:00', '13:00:00', 2587, 4),
 ('F', '07:00:00', '13:00:00', 2591, 4),
 ('F', '07:00:00', '13:00:00', 4079, 4),
 ('F', '07:00:00', '13:00:00', 4080, 4),
 ('F', '07:00:00', '14:00:00', 1023, 5),
 ('F', '07:00:00', '14:00:00', 1024, 5),
 ('F', '07:00:00', '14:00:00', 1045, 5),
 ('F', '07:00:00', '14:00:00', 1046, 5),
 ('F', '07:00:00', '14:00:00', 1091, 5),
 ('F', '07:00:00', '14:00:00', 1092, 5),
 ('F', '07:00:00', '14:00:00', 1093, 5),
 ('F', '07:00:00', '14:00:00', 2526, 5),
 ('F', '07:00:00', '14:00:00', 2527, 5),
 ('F', '07:00:00', '14:00:00', 2553, 5),
 ('F', '07:00:00', '14:00:00', 2566, 5),
 ('F', '07:00:00', '14:00:00', 2603, 5),
 ('F', '07:00:00', '14:00:00', 2604, 5),
 ('F', '07:00:00', '14:00:00', 4031, 5),
 ('F', '07:00:00', '14:00:00', 4036, 5),
 ('F', '07:00:00', '14:00:00', 4045, 5),
 ('F', '07:00:00', '14:00:00', 4085, 5),
 ('F', '07:00:00', '14:00:00', 4092, 5),
 ('F', '07:00:00', '14:00:00', 4100, 5),
 ('F', '07:00:00', '14:00:00', 5511, 5),
 ('F', '07:00:00', '14:00:00', 5512, 5),
 ('F', '07:00:00', '14:00:00', 5513, 5),
 ('F', '07:00:00', '14:00:00', 5514, 5),
 ('F', '07:00:00', '14:00:00', 5524, 5),
 ('F', '07:00:00', '14:00:00', 5525, 5),
 ('F', '07:00:00', '14:00:00', 5562, 5),
 ('F', '07:00:00', '14:00:00', 5572, 5),
 ('F', '07:00:00', '14:00:00', 5577, 5),
 ('F', '07:00:00', '14:00:00', 5581, 5),
 ('F', '07:00:00', '14:00:00', 5586, 5),
 ('F', '07:00:00', '14:00:00', 7007, 5),
 ('F', '07:00:00', '14:00:00', 7008, 5),
 ('F', '07:00:00', '14:00:00', 7009, 5),
 ('F', '07:00:00', '14:00:00', 7010, 5),
 ('F', '07:00:00', '14:00:00', 7065, 5),
 ('F', '07:00:00', '14:00:00', 7071, 5),
 ('F', '07:00:00', '14:00:00', 7084, 5),
 ('F', '07:00:00', '14:00:00', 7093, 5),
 ('F', '07:00:00', '14:00:00', 7095, 5),
 ('F', '07:00:00', '14:00:00', 7098, 5),
 ('F', '07:00:00', '14:00:00', 8443, 5),
 ('F', '07:00:00', '14:00:00', 8444, 5),
 ('F', '07:00:00', '14:00:00', 8450, 5),
 ('F', '07:00:00', '14:00:00', 8451, 5),
 ('F', '07:00:00', '14:00:00', 9854, 5),
 ('F', '07:00:00', '14:00:00', 9858, 5),
 ('F', '07:00:00', '14:00:00', 9863, 5),
 ('F', '07:00:00', '14:00:00', 9867, 5),
 ('F', '07:00:00', '14:00:00', 9879, 5),
 ('F', '07:00:00', '14:00:00', 9883, 5),
 ('F', '07:00:00', '14:00:00', 9906, 5),
 ('F', '07:00:00', '14:00:00', 11289, 5),
 ('F', '07:00:00', '14:00:00', 11291, 5),
 ('F', '07:00:00', '14:00:00', 11292, 5),
 ('F', '07:00:00', '14:00:00', 11296, 5),
 ('F', '07:00:00', '14:00:00', 11299, 5),
 ('F', '07:00:00', '14:00:00', 11301, 5),
 ('F', '07:00:00', '14:00:00', 11305, 5),
 ('F', '07:00:00', '14:00:00', 11306, 5),
 ('F', '07:00:00', '14:00:00', 11316, 5),
 ('F', '07:00:00', '14:00:00', 11317, 5),
 ('F', '07:00:00', '14:00:00', 11320, 5),
 ('F', '07:00:00', '14:00:00', 11326, 5),
 ('F', '07:00:00', '14:00:00', 12675, 5),
 ('F', '07:00:00', '14:00:00', 12678, 5),
 ('F', '07:00:00', '14:00:00', 12693, 5),
 ('F', '07:00:00', '14:00:00', 12694, 5),
 ('F', '07:00:00', '14:00:00', 12706, 5),
 ('F', '07:00:00', '14:00:00', 12707, 5),
 ('F', '07:00:00', '14:00:00', 12724, 5),
 ('F', '07:00:00', '14:00:00', 12725, 5),
 ('F', '07:00:00', '14:00:00', 12726, 5),
 ('F', '07:00:00', '14:00:00', 14107, 5),
 ('F', '07:00:00', '14:00:00', 14108, 5),
 ('F', '07:00:00', '14:00:00', 14110, 5),
 ('F', '07:00:00', '14:00:00', 14125, 5),
 ('F', '07:00:00', '14:00:00', 14126, 5),
 ('F', '07:00:00', '14:00:00', 14127, 5),
 ('F', '07:00:00', '14:00:00', 14128, 5),
 ('F', '07:00:00', '14:00:00', 14141, 5),
 ('F', '07:00:00', '14:00:00', 14142, 5),
 ('F', '07:00:00', '14:00:00', 14144, 5),
 ('F', '07:00:00', '14:00:00', 14147, 5),
 ('F', '07:00:00', '14:00:00', 14148, 5),
 ('F', '07:00:00', '14:00:00', 14150, 5),
 ('F', '07:00:00', '14:00: